## Overture Maps Foundation
According to their webpage, Overture creates reliable, easy-to-use, and interoperable open map data.
They build their maps collaboratively incorporating map data from multiple sources including Overture Members, civic organizations, and open data sources.

Overture deals with the problem that multiple datasets reference the same real-world entities using their own conventions and vocabulary, making them difficult to merge and combine. They simplify interoperability by providing a system that links entities from different data sets to the same real-world entities.

Overture is currently focused on building the following core data layers:
- administrative boundaries
- base: water, land, land use, infrastructure, land cover
- buildings
- places
- transportation

More information about their data can be found in their [documentation](https://docs.overturemaps.org/).

### Buildings layer

The Overture Maps buildings theme describes human-made structures with roofs or interior spaces that are permanently or semi-permanently in one place (source: OSM building definition). The theme includes two feature types:

- **building**: The most basic form of a building feature. The geometry is expected to be the most outer footprint -- or roofprint if traced from satellite/aerial imagery -- of a building.
- **building_part**: A single part of a building. Building parts may have the same properties as buildings. A building part is associated with a parent building via a building_id.

The documentation offers a detailed explanation about the data schema for each of the layers. For the building layer, it can be read [here](https://docs.overturemaps.org/schema/reference/buildings/building/).

The OMF’s Buildings layer includes over 780M unique building footprints worldwide. This layer has been developed by combining various open data projects including OpenStreetMap, Microsoft AI-Generated building footprints, and Esri. [Source](https://docs.overturemaps.org/guides/buildings/#14/32.58453/-117.05154/0/60).

The following example downloads building data from Overture using their Python package, which is a Beta version.

In [ ]:
# !pip install geopandas overturemaps lonboard folium

import pandas as pd
import geopandas as gpd
import overturemaps 
from shapely import wkb
from lonboard import Map, PolygonLayer
from lonboard.colormap import apply_categorical_cmap
import folium
import matplotlib.pyplot as plt

pd.set_option('display.max_columns', 500) # Allows to inspect all the columns present in the dataframe

In [ ]:
# Specify bounding box
east, south, west, north = (36.62768265193316, 37.561544985221865, 37.76386851796805, 38.460405921314695)
bbox = east, south, west, north # Use the 50km rectangle

In [ ]:
# Download builidngs from overture
table = overturemaps.record_batch_reader("building", bbox).read_all()
table = table.combine_chunks()
# Convert to dataframe
df = table.to_pandas()

In [ ]:
# Dataframe to geodataframe, set crs
gdf_overture = gpd.GeoDataFrame(
    df, 
    geometry=df['geometry'].apply(wkb.loads), 
    crs="EPSG:4326"
)

In [6]:
gdf_overture.head()

id  \
0  08b2dacae0d44fff02009cc3249b1339   
1  08b2dacae0950fff0200be1a15144db4   
2  08b2dacae0d41fff020039424d9d847e   
3  08b2dacae0c6efff0200e79f735f02a0   
4  08b2dacae0c6afff0200b0568344ad22   

                                            geometry  \
0  POLYGON ((36.62772 37.56162, 36.62757 37.56161...   
1  POLYGON ((36.62807 37.56887, 36.62812 37.56878...   
2  POLYGON ((36.62867 37.56179, 36.62867 37.5617,...   
3  POLYGON ((36.63196 37.56172, 36.63204 37.56158...   
4  POLYGON ((36.63256 37.56175, 36.63255 37.56179...   

                                                bbox  version  \
0  {'xmin': 36.627567291259766, 'xmax': 36.627731...        0   
1  {'xmin': 36.62806701660156, 'xmax': 36.6282730...        0   
2  {'xmin': 36.62866973876953, 'xmax': 36.6287651...        0   
3  {'xmin': 36.631954193115234, 'xmax': 36.632202...        0   
4  {'xmin': 36.63249969482422, 'xmax': 36.6325645...        0   

                update_time  \
0  2024-06-10T07:15:57.887Z   
1  2024-06-10T07:15:57.887Z   
2  2024-06-10T07:15:57.887Z   
3  2024-06-10T07:15:57.887Z   
4  2024-06-10T07:15:57.887Z   

                                             sources subtype names class  \
0  [{'property': '', 'dataset': 'Microsoft ML Bui...    None  None  None   
1  [{'property': '', 'dataset': 'Microsoft ML Bui...    None  None  None   
2  [{'property': '', 'dataset': 'Microsoft ML Bui...    None  None  None   
3  [{'property': '', 'dataset': 'Microsoft ML Bui...    None  None  None   
4  [{'property': '', 'dataset': 'Microsoft ML Bui...    None  None  None   

   level  has_parts  height  num_floors  min_height  min_floor facade_color  \
0    NaN      False     NaN         NaN         NaN        NaN         None   
1    NaN      False     NaN         NaN         NaN        NaN         None   
2    NaN      False     NaN         NaN         NaN        NaN         None   
3    NaN      False     NaN         NaN         NaN        NaN         None   
4    NaN      False     NaN         NaN         NaN        NaN         None   

  facade_material roof_material roof_shape  roof_direction roof_orientation  \
0            None          None       None             NaN             None   
1            None          None       None             NaN             None   
2            None          None       None             NaN             None   
3            None          None       None             NaN             None   
4            None          None       None             NaN             None   

  roof_color  roof_height  
0       None          NaN  
1       None          NaN  
2       None          NaN  
3       None          NaN  
4       None          NaN

Overture uses different sources to create their maps data. Below, it can be seen that for this region, footprints come from OpenStreet Map and from Microsoft ML Buildings. 

Below, there is a map that colors the footprint based on its source.

In [7]:
# extract the data point primary source to compare with OSM
gdf_overture['dataset'] = gdf_overture.sources.apply(lambda x: x[0]['dataset'])

In [8]:
gdf_overture.dataset.value_counts()

dataset
OpenStreetMap             160852
Microsoft ML Buildings     60504
Name: count, dtype: int64

In [10]:
gdf_overture[['geometry', 'dataset']].iloc[0:1000].explore(column = 'dataset')

### Places
The Overture Maps places theme contains datasets with point representations of real-world facilities, services, businesses, or amenities.

OMF’s Places data layer includes over 59 million POI records that have not previously been released as open data. This dataset, derived from data contributed to OMF by founding members **Meta** and **Microsoft**, provides a significant baseline of worldwide places data. The Overture community will combine the best data from all available resources, including open government data, crowdsourced local mapping data, AI/ML techniques and more to improve, update and extend the data on an ongoing basis.  The Places dataset is licensed under CDLA Permissive v2.0, a permissive open data license, and can be freely used by any map builders or location service providers.

The following example shows how to download the place layer for the area of interest. 

In [ ]:
# Download builidngs from overture
table_places = overturemaps.record_batch_reader("place", bbox).read_all()
table_places = table_places.combine_chunks()
# Convert to dataframe
df = table_places.to_pandas()

In [ ]:
# Dataframe to geodataframe, set crs
gdf_overture_plc = gpd.GeoDataFrame(
    df, 
    geometry=df['geometry'].apply(wkb.loads), 
    crs="EPSG:4326"
)

In [ ]:
# Extract the data point primary source to compare with OSM
gdf_overture_plc['dataset'] = gdf_overture_plc.sources.apply(lambda x: x[0]['dataset'])

# Extract the category
gdf_overture_plc.loc[gdf_overture_plc['categories'].notnull(), 'category'] = gdf_overture_plc.loc[gdf_overture_plc['categories'].notnull(), 'categories'].apply(lambda x: x['main'])

# Extract the primary name
gdf_overture_plc['primary_name'] = gdf_overture_plc.names.apply(lambda x: x['primary'])

In [14]:
gdf_overture_plc.head()

id                   geometry  \
0  08f2daca52169cd40340ea32cad16e2c  POINT (36.64534 37.60673)   
1  08f2daca52ab4b6d0374d46edb4e5fb4  POINT (36.64579 37.60749)   
2  08f2dacac5a7608403ff33ca64aeb9b9  POINT (36.69651 37.56686)   
3  08f2dacae1228b72035b6feec87d47a0   POINT (36.6664 37.58628)   
4  08f2dacaee1821400358b5af9f312808  POINT (36.68319 37.57333)   

                                                bbox  version  \
0  {'xmin': 36.64533996582031, 'xmax': 36.6453437...        0   
1  {'xmin': 36.645782470703125, 'xmax': 36.645786...        0   
2  {'xmin': 36.696510314941406, 'xmax': 36.696514...        0   
3  {'xmin': 36.6663932800293, 'xmax': 36.66639709...        0   
4  {'xmin': 36.68318557739258, 'xmax': 36.6831893...        0   

                update_time  \
0  2024-06-06T00:00:00.000Z   
1  2024-06-06T00:00:00.000Z   
2  2024-06-06T00:00:00.000Z   
3  2024-06-06T00:00:00.000Z   
4  2024-06-06T00:00:00.000Z   

                                             sources  \
0  [{'property': '', 'dataset': 'meta', 'record_i...   
1  [{'property': '', 'dataset': 'meta', 'record_i...   
2  [{'property': '', 'dataset': 'meta', 'record_i...   
3  [{'property': '', 'dataset': 'meta', 'record_i...   
4  [{'property': '', 'dataset': 'meta', 'record_i...   

                                               names  \
0  {'primary': 'Sır Barajı', 'common': None, 'rul...   
1  {'primary': 'Andıran Yaylası Balık Gölü', 'com...   
2  {'primary': 'Öşlü Cumhuriyeti', 'common': None...   
3  {'primary': 'Kayseri Kadir Has Stadyum', 'comm...   
4  {'primary': 'Sır Barajı', 'common': None, 'rul...   

                                         categories  confidence websites  \
0           {'main': 'aquarium', 'alternate': None}    0.490752     None   
1           {'main': 'mountain', 'alternate': None}    0.490752     None   
2                {'main': 'bar', 'alternate': None}    0.405652     None   
3     {'main': 'soccer_stadium', 'alternate': None}    0.490752     None   
4  {'main': 'lake', 'alternate': ['park', 'hotel']}    0.490752     None   

                                       socials emails phones brand  \
0   [https://www.facebook.com/177302583147408]   None   None  None   
1  [https://www.facebook.com/2164590540476898]   None   None  None   
2   [https://www.facebook.com/255621365139883]   None   None  None   
3  [https://www.facebook.com/2127245150825826]   None   None  None   
4   [https://www.facebook.com/195684563836105]   None   None  None   

                                           addresses dataset        category  \
0  [{'freeform': 'Kahraman Maras', 'locality': No...    meta        aquarium   
1  [{'freeform': None, 'locality': None, 'postcod...    meta        mountain   
2  [{'freeform': 'Öşlü Mah', 'locality': None, 'p...    meta             bar   
3  [{'freeform': None, 'locality': None, 'postcod...    meta  soccer_stadium   
4  [{'freeform': None, 'locality': 'Kahramanmaras...    meta            lake   

                 primary_name  
0                  Sır Barajı  
1  Andıran Yaylası Balık Gölü  
2            Öşlü Cumhuriyeti  
3   Kayseri Kadir Has Stadyum  
4                  Sır Barajı

The code below explores:
- Where the data comes from. In this case, it is from Meta and Microsoft. 
- The categories, a list with all OMF categories can be found [here](https://github.com/OvertureMaps/schema/blob/main/docs/schema/concepts/by-theme/places/overture_categories.csv). This example is interested in extracting health care-related facilities.
- The confidence of the existence of the place. Confidence is a number between 0 and 1. 0 means that OMF is sure that the place doesn't exist (anymore). 1 means that OMF is sure that the place exists. If there's no value for confidence, it means that OMF doesn't have any confidence information.

In [15]:
gdf_overture_plc.dataset.value_counts()

dataset
meta    9111
msft     124
Name: count, dtype: int64

In [16]:
for cat in gdf_overture_plc.category.unique():
    if cat == cat:
        if ('hospital' in cat) or ('health' in cat):
            print(cat)

hospital
health_food_store
health_and_medical
counseling_and_mental_health


In [ ]:
# Create a map to show health related facilities
m = gdf_overture_plc[gdf_overture_plc['category'].isin(['health_and_medical', 'hospital', 'counseling_and_mental_health'])][['category', 'dataset', 'geometry', 'primary_name', 'confidence', 'id']].explore(column = 'category', name = 'overture', tiles='CartoDB positron', cmap = 'viridis')
folium.LayerControl().add_to(m)
m

In [ ]:
# Create a map to show health related facilities that have a confidence greater than 0.5
m = gdf_overture_plc[(gdf_overture_plc['category'].isin(['health_and_medical', 'hospital', 'counseling_and_mental_health'])) &
                     (gdf_overture_plc['confidence']>0.5)][['category', 'dataset', 'geometry', 'primary_name', 'confidence', 'id']].explore(column = 'category', name = 'overture', tiles='CartoDB positron', cmap = 'viridis')
folium.LayerControl().add_to(m)
m

## Practice
1. Download the building footprints for a region of your interest, where the 4 introduced datasets are available, and compare the results.
2. Download hospitals and education institutions for Rio Grande do Sul State in Brasil.